In [1]:
import argparse
import os
import glob
import random
import darknet
import time
import cv2
import numpy as np
import darknet

import pymysql

#for jupyter notebook only
import sys
sys.argv=['']
del sys

def parser():
    parser = argparse.ArgumentParser(description="YOLO Object Detection")
    parser.add_argument("--input", type=str, default="",
                        help="image source. It can be a single image, a"
                        "txt with paths to them, or a folder. Image valid"
                        " formats are jpg, jpeg or png."
                        "If no input is given, ")
    parser.add_argument("--batch_size", default=1, type=int,
                        help="number of images to be processed at the same time")
    parser.add_argument("--weights", default="yolov4-p6.weights",
                        help="yolo weights path")
    parser.add_argument("--dont_show", action='store_true',
                        help="windown inference display. For headless systems")
    parser.add_argument("--ext_output", action='store_true',
                        help="display bbox coordinates of detected objects")
    parser.add_argument("--save_labels", action='store_true',
                        help="save detections bbox for each image in yolo format")
    parser.add_argument("--config_file", default="./cfg/yolov4-p6.cfg",
                        help="path to config file")
    parser.add_argument("--data_file", default="./cfg/coco.data",
                        help="path to data file")
    parser.add_argument("--thresh", type=float, default=.25,
                        help="remove detections with lower confidence")
    return parser.parse_args()


def check_arguments_errors(args):
    assert 0 < args.thresh < 1, "Threshold should be a float between zero and one (non-inclusive)"
    if not os.path.exists(args.config_file):
        raise(ValueError("Invalid config path {}".format(os.path.abspath(args.config_file))))
    if not os.path.exists(args.weights):
        raise(ValueError("Invalid weight path {}".format(os.path.abspath(args.weights))))
    if not os.path.exists(args.data_file):
        raise(ValueError("Invalid data file path {}".format(os.path.abspath(args.data_file))))
    if args.input and not os.path.exists(args.input):
        raise(ValueError("Invalid image path {}".format(os.path.abspath(args.input))))


def check_batch_shape(images, batch_size):
    """
        Image sizes should be the same width and height
    """
    shapes = [image.shape for image in images]
    if len(set(shapes)) > 1:
        raise ValueError("Images don't have same shape")
    if len(shapes) > batch_size:
        raise ValueError("Batch size higher than number of images")
    return shapes[0]


def load_images(images_path):
    """
    If image path is given, return it directly
    For txt file, read it and return each line as image path
    In other case, it's a folder, return a list with names of each
    jpg, jpeg and png file
    """
    input_path_extension = images_path.split('.')[-1]
    if input_path_extension in ['jpg', 'jpeg', 'png']:
        return [images_path]
    elif input_path_extension == "txt":
        with open(images_path, "r") as f:
            return f.read().splitlines()
    else:
        return glob.glob(
            os.path.join(images_path, "*.jpg")) + \
            glob.glob(os.path.join(images_path, "*.png")) + \
            glob.glob(os.path.join(images_path, "*.jpeg"))


def prepare_batch(images, network, channels=3):
    width = darknet.network_width(network)
    height = darknet.network_height(network)

    darknet_images = []
    for image in images:
        image_rgb = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
        image_resized = cv2.resize(image_rgb, (width, height),
                                   interpolation=cv2.INTER_LINEAR)
        custom_image = image_resized.transpose(2, 0, 1)
        darknet_images.append(custom_image)

    batch_array = np.concatenate(darknet_images, axis=0)
    batch_array = np.ascontiguousarray(batch_array.flat, dtype=np.float32)/255.0
    darknet_images = batch_array.ctypes.data_as(darknet.POINTER(darknet.c_float))
    return darknet.IMAGE(width, height, channels, darknet_images)


def image_detection(image_path, network, class_names, class_colors, thresh):
    # Darknet doesn't accept numpy images.
    # Create one with image we reuse for each detect
    width = darknet.network_width(network)
    height = darknet.network_height(network)
    darknet_image = darknet.make_image(width, height, 3)

    image = cv2.imread(image_path)
    image_rgb = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
    image_resized = cv2.resize(image_rgb, (width, height),
                               interpolation=cv2.INTER_LINEAR)

    darknet.copy_image_from_bytes(darknet_image, image_resized.tobytes())
    detections = darknet.detect_image(network, class_names, darknet_image, thresh=thresh)
    darknet.free_image(darknet_image)
    image = darknet.draw_boxes(detections, image_resized, class_colors)
    return cv2.cvtColor(image, cv2.COLOR_BGR2RGB), detections


def batch_detection(network, images, class_names, class_colors,
                    thresh=0.25, hier_thresh=.5, nms=.45, batch_size=4):
    image_height, image_width, _ = check_batch_shape(images, batch_size)
    darknet_images = prepare_batch(images, network)
    batch_detections = darknet.network_predict_batch(network, darknet_images, batch_size, image_width,
                                                     image_height, thresh, hier_thresh, None, 0, 0)
    batch_predictions = []
    for idx in range(batch_size):
        num = batch_detections[idx].num
        detections = batch_detections[idx].dets
        if nms:
            darknet.do_nms_obj(detections, num, len(class_names), nms)
        predictions = darknet.remove_negatives(detections, class_names, num)
        images[idx] = darknet.draw_boxes(predictions, images[idx], class_colors)
        batch_predictions.append(predictions)
    darknet.free_batch_detections(batch_detections, batch_size)
    return images, batch_predictions


def image_classification(image, network, class_names):
    width = darknet.network_width(network)
    height = darknet.network_height(network)
    image_rgb = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
    image_resized = cv2.resize(image_rgb, (width, height),
                                interpolation=cv2.INTER_LINEAR)
    darknet_image = darknet.make_image(width, height, 3)
    darknet.copy_image_from_bytes(darknet_image, image_resized.tobytes())
    detections = darknet.predict_image(network, darknet_image)
    predictions = [(name, detections[idx]) for idx, name in enumerate(class_names)]
    darknet.free_image(darknet_image)
    return sorted(predictions, key=lambda x: -x[1])


def convert2relative(image, bbox):
    """
    YOLO format use relative coordinates for annotation
    """
    x, y, w, h = bbox
    height, width, _ = image.shape
    return x/width, y/height, w/width, h/height


def save_annotations(name, image, detections, class_names):
    """
    Files saved with image_name.txt and relative coordinates
    """
    file_name = os.path.splitext(name)[0] + ".txt"
    with open(file_name, "w") as f:
        for label, confidence, bbox in detections:
            x, y, w, h = convert2relative(image, bbox)
            label = class_names.index(label)
            f.write("{} {:.4f} {:.4f} {:.4f} {:.4f} {:.4f}\n".format(label, x, y, w, h, float(confidence)))


def batch_detection_example():
    args = parser()
    check_arguments_errors(args)
    batch_size = 3
    random.seed(3)  # deterministic bbox colors
    network, class_names, class_colors = darknet.load_network(
        args.config_file,
        args.data_file,
        args.weights,
        batch_size=batch_size
    )
    image_names = ['data/horses.jpg', 'data/horses.jpg', 'data/eagle.jpg']
    images = [cv2.imread(image) for image in image_names]
    images, detections,  = batch_detection(network, images, class_names,
                                           class_colors, batch_size=batch_size)
    for name, image in zip(image_names, images):
        cv2.imwrite(name.replace("data/", ""), image)
    print(detections)


def main():
    args = parser()
    check_arguments_errors(args)
    
    random.seed(3)  # deterministic bbox colors
    network, class_names, class_colors = darknet.load_network(
        args.config_file,
        args.data_file,
        args.weights,
        batch_size=args.batch_size
    )
    images_src = input("Enter Image or Text Path: ")
    print(images_src)
    images = load_images(images_src)
    out_dir = images_src.rsplit('\\',1)[0] + '\\output\\'
    if(not os.path.exists(out_dir)):
                os.mkdir(out_dir)
    index = 0
    while True:
        # loop asking for new image paths if no list is given
        if len(images) > 1 and index < len(images):
            if index >= len(images):
                break
            image_name = images[index]
        else:
            image_name = input("Enter Image Path: ")
        prev_time = time.time()
        image, detections = image_detection(
            image_name, network, class_names, class_colors, args.thresh
            )
        if args.save_labels:
            save_annotations(image_name, image, detections, class_names)
        darknet.print_detections(detections, args.ext_output)
        fps = int(1/(time.time() - prev_time))
        print("FPS: {}".format(fps))
        add_to_db(image_name, detections)
        if not args.dont_show:
            #cv2.imshow('Inference', image)
            out_path = out_dir + (image_name.rsplit('\\',1)[1])
            cv2.imwrite(out_path, image)
            if cv2.waitKey() & 0xFF == ord('q'):
                break
        conn.commit()
        index += 1

In [2]:
# COCO Class names
# Index of the class in the list is its ID. For example, to get ID of
# the teddy bear class, use: class_names.index('teddy bear')
class_names = ['BG', 'person', 'bicycle', 'car', 'motorcycle', 'airplane',
               'bus', 'train', 'truck', 'boat', 'traffic light',
               'fire hydrant', 'stop sign', 'parking meter', 'bench', 'bird',
               'cat', 'dog', 'horse', 'sheep', 'cow', 'elephant', 'bear',
               'zebra', 'giraffe', 'backpack', 'umbrella', 'handbag', 'tie',
               'suitcase', 'frisbee', 'skis', 'snowboard', 'sports ball',
               'kite', 'baseball bat', 'baseball glove', 'skateboard',
               'surfboard', 'tennis racket', 'bottle', 'wine glass', 'cup',
               'fork', 'knife', 'spoon', 'bowl', 'banana', 'apple',
               'sandwich', 'orange', 'broccoli', 'carrot', 'hot dog', 'pizza',
               'donut', 'cake', 'chair', 'couch', 'potted plant', 'bed',
               'dining table', 'toilet', 'tv', 'laptop', 'mouse', 'remote',
               'keyboard', 'cell phone', 'microwave', 'oven', 'toaster',
               'sink', 'refrigerator', 'book', 'clock', 'vase', 'scissors',
               'teddy bear', 'hair drier', 'toothbrush']

In [3]:
#DB Connection
conn = pymysql.connect(host='localhost',  
                       port=3306,  
                       user='root',  
                       passwd='xRemixeDx1997',  
                       db='darknet',  
                       charset='utf8')

In [3]:
conn = pymysql.connect(host='localhost',  
                       port=3306,  
                       user='root',  
                       passwd='xRemixeDx1997',  
                       db='darknet',  
                       charset='utf8')  
cur = conn.cursor()
sql = "CREATE TABLE images (" + os.linesep + "img_name varchar(255) not null,"
sql += os.linesep + "img_path varchar(255) not null,"
sql += os.linesep + "out_path varchar(255) not null,"
for i in range(len(class_names)):
    sql += os.linesep + " " + class_names[i].replace(" ","_") + " BIT(1),"
sql += os.linesep + "primary key (img_name)"
sql = sql.rstrip(",") + ");"
cur.execute(sql)
print(sql)
output = cur.fetchall()
print(output)
conn.commit()

# close connection to the database  
# cur.close()  
# conn.close()

CREATE TABLE images (
img_name varchar(255) not null,
img_path varchar(255) not null,
out_path varchar(255) not null,
 BG BIT(1),
 person BIT(1),
 bicycle BIT(1),
 car BIT(1),
 motorcycle BIT(1),
 airplane BIT(1),
 bus BIT(1),
 train BIT(1),
 truck BIT(1),
 boat BIT(1),
 traffic_light BIT(1),
 fire_hydrant BIT(1),
 stop_sign BIT(1),
 parking_meter BIT(1),
 bench BIT(1),
 bird BIT(1),
 cat BIT(1),
 dog BIT(1),
 horse BIT(1),
 sheep BIT(1),
 cow BIT(1),
 elephant BIT(1),
 bear BIT(1),
 zebra BIT(1),
 giraffe BIT(1),
 backpack BIT(1),
 umbrella BIT(1),
 handbag BIT(1),
 tie BIT(1),
 suitcase BIT(1),
 frisbee BIT(1),
 skis BIT(1),
 snowboard BIT(1),
 sports_ball BIT(1),
 kite BIT(1),
 baseball_bat BIT(1),
 baseball_glove BIT(1),
 skateboard BIT(1),
 surfboard BIT(1),
 tennis_racket BIT(1),
 bottle BIT(1),
 wine_glass BIT(1),
 cup BIT(1),
 fork BIT(1),
 knife BIT(1),
 spoon BIT(1),
 bowl BIT(1),
 banana BIT(1),
 apple BIT(1),
 sandwich BIT(1),
 orange BIT(1),
 broccoli BIT(1),
 carrot BIT(1

In [4]:
def add_to_db(image_name, detections, thresh=0.5):
    unique_labels = set([])
    name = image_name.rsplit('\\',1)[1].split('.')[0]
    outdir = image_name.rsplit('\\',1)[0] + '\\\\output\\\\' + image_name.rsplit('\\',1)[1]

    for label, confidence, bbox in detections:
        if int(confidence.split('.')[0]) > thresh:
            unique_labels.add(label)
    print(unique_labels)
    
    cur = conn.cursor()
    sql = "INSERT INTO images (img_name, img_path, out_path, "
    for i in range(len(class_names)):
        sql += class_names[i].replace(" ","_") + ", "
    sql = sql.rstrip(", ") + ") " + os.linesep + "VALUES (%s, %s, %s, "
    
    for i in range(len(class_names)):
        if class_names[i] in unique_labels:
            sql += "1, "
        else:
            sql += "0, "
    sql = sql.rstrip(", ") + ");"
    print(sql)
    cur.execute(sql, (name, image_name, outdir))
    output = cur.fetchall()
    

In [ ]:
main()

Enter Image or Text Path: E:\Programme\COCO\val2017\test.txt
E:\Programme\COCO\val2017\test.txt

Objects:
chair: 28.58%
refrigerator: 32.16%
diningtable: 35.33%
pottedplant: 53.4%
refrigerator: 57.96%
pottedplant: 61.1%
vase: 61.98%
person: 64.25%
vase: 65.15%
clock: 67.33%
chair: 71.93%
diningtable: 73.18%
vase: 74.46%
vase: 80.23%
chair: 81.75%
vase: 86.07%
person: 86.32%
tvmonitor: 91.33%
FPS: 1
{'chair', 'person', 'refrigerator', 'clock', 'tvmonitor', 'pottedplant', 'vase', 'diningtable'}
INSERT INTO images (img_name, img_path, out_path, BG, person, bicycle, car, motorcycle, airplane, bus, train, truck, boat, traffic_light, fire_hydrant, stop_sign, parking_meter, bench, bird, cat, dog, horse, sheep, cow, elephant, bear, zebra, giraffe, backpack, umbrella, handbag, tie, suitcase, frisbee, skis, snowboard, sports_ball, kite, baseball_bat, baseball_glove, skateboard, surfboard, tennis_racket, bottle, wine_glass, cup, fork, knife, spoon, bowl, banana, apple, sandwich, orange, broccoli,


Objects:
sports ball: 53.61%
person: 67.19%
person: 85.95%
FPS: 4
{'sports ball', 'person'}
INSERT INTO images (img_name, img_path, out_path, BG, person, bicycle, car, motorcycle, airplane, bus, train, truck, boat, traffic_light, fire_hydrant, stop_sign, parking_meter, bench, bird, cat, dog, horse, sheep, cow, elephant, bear, zebra, giraffe, backpack, umbrella, handbag, tie, suitcase, frisbee, skis, snowboard, sports_ball, kite, baseball_bat, baseball_glove, skateboard, surfboard, tennis_racket, bottle, wine_glass, cup, fork, knife, spoon, bowl, banana, apple, sandwich, orange, broccoli, carrot, hot_dog, pizza, donut, cake, chair, couch, potted_plant, bed, dining_table, toilet, tv, laptop, mouse, remote, keyboard, cell_phone, microwave, oven, toaster, sink, refrigerator, book, clock, vase, scissors, teddy_bear, hair_drier, toothbrush) 
VALUES (%s, %s, %s, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,


Objects:
surfboard: 81.07%
person: 92.82%
FPS: 4
{'surfboard', 'person'}
INSERT INTO images (img_name, img_path, out_path, BG, person, bicycle, car, motorcycle, airplane, bus, train, truck, boat, traffic_light, fire_hydrant, stop_sign, parking_meter, bench, bird, cat, dog, horse, sheep, cow, elephant, bear, zebra, giraffe, backpack, umbrella, handbag, tie, suitcase, frisbee, skis, snowboard, sports_ball, kite, baseball_bat, baseball_glove, skateboard, surfboard, tennis_racket, bottle, wine_glass, cup, fork, knife, spoon, bowl, banana, apple, sandwich, orange, broccoli, carrot, hot_dog, pizza, donut, cake, chair, couch, potted_plant, bed, dining_table, toilet, tv, laptop, mouse, remote, keyboard, cell_phone, microwave, oven, toaster, sink, refrigerator, book, clock, vase, scissors, teddy_bear, hair_drier, toothbrush) 
VALUES (%s, %s, %s, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 


Objects:
traffic light: 44.91%
tie: 50.25%
person: 77.63%
person: 85.28%
person: 92.96%
bus: 94.22%
FPS: 4
{'tie', 'bus', 'person', 'traffic light'}
INSERT INTO images (img_name, img_path, out_path, BG, person, bicycle, car, motorcycle, airplane, bus, train, truck, boat, traffic_light, fire_hydrant, stop_sign, parking_meter, bench, bird, cat, dog, horse, sheep, cow, elephant, bear, zebra, giraffe, backpack, umbrella, handbag, tie, suitcase, frisbee, skis, snowboard, sports_ball, kite, baseball_bat, baseball_glove, skateboard, surfboard, tennis_racket, bottle, wine_glass, cup, fork, knife, spoon, bowl, banana, apple, sandwich, orange, broccoli, carrot, hot_dog, pizza, donut, cake, chair, couch, potted_plant, bed, dining_table, toilet, tv, laptop, mouse, remote, keyboard, cell_phone, microwave, oven, toaster, sink, refrigerator, book, clock, vase, scissors, teddy_bear, hair_drier, toothbrush) 
VALUES (%s, %s, %s, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,


Objects:
person: 85.72%
skis: 86.71%
person: 89.26%
person: 92.91%
person: 93.72%
FPS: 4
{'person', 'skis'}
INSERT INTO images (img_name, img_path, out_path, BG, person, bicycle, car, motorcycle, airplane, bus, train, truck, boat, traffic_light, fire_hydrant, stop_sign, parking_meter, bench, bird, cat, dog, horse, sheep, cow, elephant, bear, zebra, giraffe, backpack, umbrella, handbag, tie, suitcase, frisbee, skis, snowboard, sports_ball, kite, baseball_bat, baseball_glove, skateboard, surfboard, tennis_racket, bottle, wine_glass, cup, fork, knife, spoon, bowl, banana, apple, sandwich, orange, broccoli, carrot, hot_dog, pizza, donut, cake, chair, couch, potted_plant, bed, dining_table, toilet, tv, laptop, mouse, remote, keyboard, cell_phone, microwave, oven, toaster, sink, refrigerator, book, clock, vase, scissors, teddy_bear, hair_drier, toothbrush) 
VALUES (%s, %s, %s, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0

...


Objects:
remote: 28.23%
remote: 32.55%
sofa: 41.95%
person: 43.04%
person: 47.73%
book: 59.02%
bottle: 69.58%
person: 74.1%
bottle: 77.36%
person: 87.13%
person: 88.43%
person: 89.1%
person: 92.02%
remote: 92.89%
FPS: 4
{'book', 'person', 'remote', 'bottle', 'sofa'}
INSERT INTO images (img_name, img_path, out_path, BG, person, bicycle, car, motorcycle, airplane, bus, train, truck, boat, traffic_light, fire_hydrant, stop_sign, parking_meter, bench, bird, cat, dog, horse, sheep, cow, elephant, bear, zebra, giraffe, backpack, umbrella, handbag, tie, suitcase, frisbee, skis, snowboard, sports_ball, kite, baseball_bat, baseball_glove, skateboard, surfboard, tennis_racket, bottle, wine_glass, cup, fork, knife, spoon, bowl, banana, apple, sandwich, orange, broccoli, carrot, hot_dog, pizza, donut, cake, chair, couch, potted_plant, bed, dining_table, toilet, tv, laptop, mouse, remote, keyboard, cell_phone, microwave, oven, toaster, sink, refrigerator, book, clock, vase, scissors, teddy_bear, h


Objects:
cup: 27.05%
bowl: 27.77%
cup: 36.23%
cup: 38.68%
diningtable: 40.0%
person: 41.05%
diningtable: 41.86%
chair: 45.02%
chair: 51.75%
bottle: 53.1%
chair: 54.16%
chair: 55.4%
bottle: 55.49%
cup: 56.63%
cup: 57.53%
tie: 69.17%
person: 72.64%
bottle: 73.65%
person: 75.21%
diningtable: 76.0%
cup: 77.25%
bottle: 80.03%
chair: 80.54%
cup: 81.97%
cup: 83.33%
cup: 84.66%
cup: 85.97%
wine glass: 86.12%
person: 86.67%
cup: 86.84%
cup: 87.44%
cup: 87.5%
cup: 88.16%
cup: 88.62%
cup: 88.76%
cup: 89.05%
cup: 89.57%
cup: 89.65%
cup: 90.45%
cup: 90.76%
cup: 91.08%
person: 93.1%
cup: 93.32%
person: 94.3%
FPS: 4
{'tie', 'chair', 'person', 'wine glass', 'bottle', 'cup', 'bowl', 'diningtable'}
INSERT INTO images (img_name, img_path, out_path, BG, person, bicycle, car, motorcycle, airplane, bus, train, truck, boat, traffic_light, fire_hydrant, stop_sign, parking_meter, bench, bird, cat, dog, horse, sheep, cow, elephant, bear, zebra, giraffe, backpack, umbrella, handbag, tie, suitcase, frisbee, skis


Objects:
person: 42.49%
person: 65.57%
train: 87.24%
FPS: 4
{'train', 'person'}
INSERT INTO images (img_name, img_path, out_path, BG, person, bicycle, car, motorcycle, airplane, bus, train, truck, boat, traffic_light, fire_hydrant, stop_sign, parking_meter, bench, bird, cat, dog, horse, sheep, cow, elephant, bear, zebra, giraffe, backpack, umbrella, handbag, tie, suitcase, frisbee, skis, snowboard, sports_ball, kite, baseball_bat, baseball_glove, skateboard, surfboard, tennis_racket, bottle, wine_glass, cup, fork, knife, spoon, bowl, banana, apple, sandwich, orange, broccoli, carrot, hot_dog, pizza, donut, cake, chair, couch, potted_plant, bed, dining_table, toilet, tv, laptop, mouse, remote, keyboard, cell_phone, microwave, oven, toaster, sink, refrigerator, book, clock, vase, scissors, teddy_bear, hair_drier, toothbrush) 
VALUES (%s, %s, %s, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,


Objects:
car: 31.21%
person: 31.7%
stop sign: 53.63%
car: 73.3%
stop sign: 75.87%
car: 87.6%
cow: 88.14%
car: 88.48%
cow: 92.02%
cow: 93.73%
FPS: 4
{'person', 'car', 'cow', 'stop sign'}
INSERT INTO images (img_name, img_path, out_path, BG, person, bicycle, car, motorcycle, airplane, bus, train, truck, boat, traffic_light, fire_hydrant, stop_sign, parking_meter, bench, bird, cat, dog, horse, sheep, cow, elephant, bear, zebra, giraffe, backpack, umbrella, handbag, tie, suitcase, frisbee, skis, snowboard, sports_ball, kite, baseball_bat, baseball_glove, skateboard, surfboard, tennis_racket, bottle, wine_glass, cup, fork, knife, spoon, bowl, banana, apple, sandwich, orange, broccoli, carrot, hot_dog, pizza, donut, cake, chair, couch, potted_plant, bed, dining_table, toilet, tv, laptop, mouse, remote, keyboard, cell_phone, microwave, oven, toaster, sink, refrigerator, book, clock, vase, scissors, teddy_bear, hair_drier, toothbrush) 
VALUES (%s, %s, %s, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1


Objects:
toilet: 35.47%
toilet: 56.49%
toilet: 88.69%
FPS: 4
{'toilet'}
INSERT INTO images (img_name, img_path, out_path, BG, person, bicycle, car, motorcycle, airplane, bus, train, truck, boat, traffic_light, fire_hydrant, stop_sign, parking_meter, bench, bird, cat, dog, horse, sheep, cow, elephant, bear, zebra, giraffe, backpack, umbrella, handbag, tie, suitcase, frisbee, skis, snowboard, sports_ball, kite, baseball_bat, baseball_glove, skateboard, surfboard, tennis_racket, bottle, wine_glass, cup, fork, knife, spoon, bowl, banana, apple, sandwich, orange, broccoli, carrot, hot_dog, pizza, donut, cake, chair, couch, potted_plant, bed, dining_table, toilet, tv, laptop, mouse, remote, keyboard, cell_phone, microwave, oven, toaster, sink, refrigerator, book, clock, vase, scissors, teddy_bear, hair_drier, toothbrush) 
VALUES (%s, %s, %s, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0